# Static Visualization Draft

Description of project

Data Sources

Narrative, questions

In [4]:
import pandas as pd
import altair as alt

In [5]:
#National Database of Childcare Prices (NDCP)
#NDCP state-level summary data
state_lvl_df = pd.read_excel(r'c:/Users/calli/capp24/Fall 25/Data Visualization/capp30239/data/state_level_est.xlsx')
#NDCP county-level data for each state
big_22_ndcp_df = pd.read_excel(r'C:/Users/calli/capp24/Fall 25/Data Visualization/capp30239/data/ndcp2022.xlsx')
#Census state-level Median Household Income
census_mhi_df = pd.read_csv(r'C:/Users/calli/capp24/Fall 25/Data Visualization/capp30239/data/census_mhi_2022.csv')
#Regulatory ranking data from West Virginia University and
#thinktank Child Care Aware of America
regulations_df = pd.read_csv(r"C:/Users/calli/capp24/Fall 25/Data Visualization/capp30239/data/regulatory rankings.csv")


In [3]:
state_lvl_df = pd.read_excel('state_level_est.xlsx')

FileNotFoundError: [Errno 2] No such file or directory: 'state_level_est.xlsx'

In [3]:
census_mhi_df = pd.read_csv('census_mhi_2022.csv')
census_mhi_df = census_mhi_df.rename(columns={"State":"STATE_NAME", "MHI":"MHI"})

In [4]:
big_22_ndcp_df = pd.read_excel('2022ndcp.xlsx')

In [5]:
big_22_ndcp_df.shape

(48308, 370)

## Graph Set One

Grouped bar charts looking at childcare cost by developmental cohort. I look at both national level and Illinois level data. 

Currently I think the number of subgraphs is overwhelming, and I'm wondering if there's a better graph type or way that I could subsection the current graphs to be more digestible. 

Another area where I'd appreciate feedback (in general, but particularly here) is color. Normally nominal data will use categorical color schemes, but you could also consider the age cohorts to be ordered data, in which case, perhaps a sequential color scheme would be more appropriate. Thoughts?

In [4]:
#state avg cost data
def state_avg_costs_df(df):
    #2022 center data
    #eliminate states that don't have data for all four age groups
    #eliminate states where less than 90% of kids are living in counties w data
    clean_df = df[(df['STUDYYEAR'] == 2022) & (df['MEDIAN_INFANT_PRICE'].notna()) & (df['TYPE'] == 'Center') & (df['PCT_VALID_INFANT'] >= .9) & (df['PCT_VALID_TODDLER'] >= .9) & (df['PCT_VALID_PRESCHOOL'] >= .9) & (df['PCT_VALID_SCHOOLAGE'] >= .9)]
    select_columns_df = clean_df[['STATE_NAME', 'MEDIAN_INFANT_PRICE', 'MEDIAN_TODDLER_PRICE', 'MEDIAN_PRESCHOOL_PRICE', 'MEDIAN_SCHOOLAGE_PRICE']]
    
    return select_columns_df

In [5]:
def grouped_bar_df(df, census_df):
    df = df.melt(
        id_vars=['STATE_NAME'],
        value_vars=['MEDIAN_INFANT_PRICE', 'MEDIAN_TODDLER_PRICE', 'MEDIAN_PRESCHOOL_PRICE', 'MEDIAN_SCHOOLAGE_PRICE'],
        var_name='age',
        value_name='price'
    )
    df['age'] = df['age'].str.replace('_PRICE', '').str.replace('MEDIAN_', '').str.lower()
    merged = pd.merge(df, census_df, "left", "STATE_NAME")
    merged["adjusted price"] = merged['price'] * 52 / merged['MHI']

    return merged

In [11]:
kwargs = {"title": "title", "x": "xvar", "xlab": "x_label", "y": "yvar", "ylab": "y_label"}

In [14]:
def groupedbar(df):
    '''
    Grouped bar graph of cost burden by age cohort for a selection of states.
    '''
    # #load in data
    # df = grouped_bar_df()
    
    #order for bars
    age_order = ['infant', 'toddler', 'preschool', 'schoolage']
    
    chart = alt.Chart(df)
    
    #form bars
    bars = chart.mark_bar().encode(
        alt.X('age:N', sort=age_order).title('Age Group'),
        alt.Y('adjusted price:Q').axis(format='%').title('Percentage Income Spent for One Child'),
        alt.Color('age:N').scale(scheme='turbo').sort(age_order).title('Age Group'),
    )
    
    #DHHS 7% line
    line = chart.mark_rule(color='black', strokeDash=[4,2]).encode(y=alt.datum(0.07))

    final = bars + line

    final.facet(facet=alt.Facet('STATE_NAME:N',title=None), columns=5).properties(
        title="2022 Childcare Costs Normalized by State Median Family Income"
        ).show()

In [13]:
def groupedbar(df, title, norm, level_name):
    age_order = ['infant', 'toddler', 'preschool', 'schoolage']

    chart = alt.Chart(df)

    bars = chart.mark_bar().encode(
        alt.X('age:N', sort=age_order).title('Age Group'),
        alt.Y(f'{norm}:Q').axis(format='%').title('Percentage Income Expenditure for One Child'),
        alt.Color('age:N').scale(scheme='turbo').sort(age_order).title('Age Group'),
    )
    
    line = chart.mark_rule(color='black', strokeDash=[4,2]).encode(y=alt.datum(0.07))
    
    final = bars + line


    final.facet(facet=alt.Facet(
        f'{level_name}:N',
        title=None),
        ).properties(title=title).configure_view(fill=None).show()

In [ ]:
def cohortbar(df, title, norm, level_name):
    age_order = ['infant', 'toddler', 'preschool', 'schoolage']
    alt.Chart(df).mark_bar().encode(
        alt.X(f'{level_name}:N').title('Age Group'),
        alt.Y(f'{norm}:Q').title('Weekly Cost of Childcare for One Child'),
        alt.Color('age:N').scale(scheme='turbo'),
        # column=f'{level_name}:N'
    ).facet('age:N', columns=1).properties(title=title).show()

### National, State Level, *Not* Normalized

In [6]:
state_avgs = state_avg_costs_df(state_lvl_df)
grouped_df = grouped_bar_df(state_avgs, census_mhi_df)
groupedbar(grouped_df, "2022 Weekly Childcare Cost by State", "price", "STATE_NAME")

NameError: name 'groupedbar' is not defined

In [12]:
len(grouped_df[grouped_df['adjusted price'] <= .07]['STATE_NAME'].unique())

8

In [13]:
8/41

0.1951219512195122

### National, State Level, Normalized

In [28]:
reg_df = regulations_df

In [17]:
reg_df.head()

STATE_NAME  Restrictiveness  R Index  Final Q Score Pct of Possible  \
0     Alabama               47     8.12             67             45%   
1      Alaska               21     3.15             88             59%   
2     Arizona               46     7.90             96             64%   
3    Arkansas               35     5.73             82             55%   
4  California               37     5.84             51             34%   

   Quality  
0       46  
1       33  
2       20  
3       39  
4       48

In [89]:
parallel_df = grouped_df[grouped_df["age"] == 'schoolage'].sort_values('adjusted price', ascending=False)

In [67]:
parallel_df = grouped_df[grouped_df["age"] == 'infant'].sort_values('adjusted price', ascending=False)

In [19]:
grouped_df[grouped_df["age"] == 'infant'].sort_values('adjusted price', ascending=False)

STATE_NAME     age   price    MHI  adjusted price
16   Massachusetts  infant  461.55  94488        0.254007
18       Minnesota  infant  390.00  82338        0.246302
28            Ohio  infant  295.00  65720        0.233414
30          Oregon  infant  329.44  75657        0.226428
3         Colorado  infant  377.40  89302        0.219758
2       California  infant  379.21  91551        0.215387
40       Wisconsin  infant  293.00  70996        0.214604
4      Connecticut  infant  350.00  88429        0.205815
38      Washington  infant  357.31  91306        0.203493
22          Nevada  infant  275.63  72333        0.198150
25        New York  infant  300.00  79557        0.196086
9         Illinois  infant  278.33  76708        0.188679
1          Arizona  infant  270.00  74568        0.188285
29        Oklahoma  infant  215.46  59673        0.187755
31    Rhode Island  infant  289.59  81854        0.183970
21        Nebraska  infant  243.75  69597        0.182120
15        Maryland  infant  327.39  94991        0.179220
5         Delaware  infant  280.28  82174        0.177362
23   New Hampshire  infant  300.05  89992        0.173378
14           Maine  infant  230.00  69543        0.171980
20         Montana  infant  220.81  67631        0.169776
24      New Jersey  infant  313.73  96346        0.169327
6          Florida  infant  225.00  69303        0.168824
34       Tennessee  infant  211.67  65254        0.168677
32  South Carolina  infant  198.93  64115        0.161341
39   West Virginia  infant  167.49  54329        0.160310
26  North Carolina  infant  202.52  67481        0.156059
27    North Dakota  infant  213.81  71970        0.154483
37        Virginia  infant  246.72  85873        0.149400
7          Georgia  infant  205.00  72837        0.146354
13       Louisiana  infant  153.33  55416        0.143878
17        Michigan  infant  173.20  66986        0.134452
35           Texas  infant  185.00  72284        0.133086
12        Kentucky  infant  151.30  59341        0.132583
36            Utah  infant  226.27  89168        0.131954
10            Iowa  infant  165.98  69588        0.124029
8            Idaho  infant  166.41  72785        0.118889
11          Kansas  infant  157.33  68925        0.118697
0          Alabama  infant  136.01  59674        0.118519
19     Mississippi  infant  118.68  52719        0.117061
33    South Dakota  infant  150.00  69728        0.111863

In [90]:
ranking = list(range(1,42))

In [91]:
parallel_df['Cost Burden'] = ranking

In [92]:
parallel_df = parallel_df[(parallel_df["Cost Burden"] < 6) | (parallel_df["Cost Burden"] > 36)]

In [93]:
parallel_df = parallel_df.merge(reg_df, "left", "STATE_NAME")

In [94]:
parallel_df = pd.melt(parallel_df, id_vars=['STATE_NAME'], value_vars=['Restrictiveness', 'Quality', 'Cost Burden'])

In [95]:
def create_new_column(row):
    if row['variable'] == "Restrictiveness":
        return 0
    elif row['variable'] == "Quality":
        return 1
    else:
        return 2

parallel_df['Rank_Type'] = parallel_df.apply(create_new_column, axis=1)

In [36]:
parallel_df.head()

STATE_NAME         variable  value  Rank_Type
0     Nevada  Restrictiveness     44          0
1    Montana  Restrictiveness     42          0
2  Wisconsin  Restrictiveness     11          0
3  Minnesota  Restrictiveness      7          0
4   New York  Restrictiveness      2          0

In [298]:
chart = alt.Chart(parallel_df, title=alt.Title(['School Aged Children'], anchor='middle', offset=40))

state_domain = parallel_df['STATE_NAME'].unique()
color_range = ["#4a58dd", "#dedd32", "#2f9df5", "#f65f18", "#4df884", "#7bda3c", "#ffa423", "#27d7c4", "#ba2208", "#cb3bc6"]

cat_order = ["Restrictiveness", "Quality", "Cost Burden"]

lines = chart.mark_line().encode(
    alt.X("Rank_Type:O", title=None, axis=None),
    alt.Y("value:O", axis=None),
    alt.Color("STATE_NAME:N", legend=None, scale=alt.Scale(domain=state_domain, range=color_range))
).properties(
    width=350, height=500
)

# Use the `argmax` aggregate to limit the dataset to the final value
label = chart.encode(
    alt.X('max(Rank_Type):O'),
    alt.Y('value:O').aggregate(argmax='Rank_Type'),
    text='STATE_NAME'
)

vertical_line = chart.mark_rule(color='black').encode(
        x='Rank_Type:O'
    )

# Create a text label
text = label.mark_text(align='left', dx=4, dy=0)

final = lines + text + vertical_line

final.configure_axis(grid=False).configure_view(stroke=None).show()

alt.LayerChart(...)

In [ ]:
chart = alt.Chart(parallel_df)

state_domain = parallel_df['STATE_NAME'].unique()
color_range = ["#4a58dd", "#dedd32", "#2f9df5", "#f65f18", "#4df884", "#7bda3c", "#ffa423", "#27d7c4", "#ba2208", "#cb3bc6"]

lines = chart.mark_line().encode(
    alt.X("Rank_Type:O", title=None, axis=alt.Axis(labelAngle= 0, domain=False, orient='top', ticks=False)),
    alt.Y("value:O", axis=None),
    alt.Color("STATE_NAME:N", legend=None, scale=alt.Scale(domain=state_domain, range=color_range))
).properties(
    width=350
)

# Use the `argmax` aggregate to limit the dataset to the final value
label = chart.encode(
    alt.X('max(Rank_Type):O'),
    alt.Y('value:O').aggregate(argmax='Rank_Type'),
    text='STATE_NAME'
)

vertical_line = chart.mark_rule(color='black').encode(
        x='Rank_Type:O'
    )

# Create a text label
text = label.mark_text(align='left', dx=4, dy=0)

final = lines + text + vertical_line

final.configure_axis(grid=False).configure_view(stroke=None).show()

alt.LayerChart(...)

In [38]:
examples = ['Illinois', 'Massachusetts', 'Texas', 'Montana', 'California']
g_df = grouped_df[grouped_df['STATE_NAME'].isin(examples)]

In [303]:
groupedbar(g_df, "2022 Childcare Costs Normalized by State Median Family Income",
                    "adjusted price", "STATE_NAME")

alt.FacetChart(...)

In [ ]:
cohortbar(grouped_df, "2022 Childcare Costs Normalized by State Median Family Income",
                    "adjusted price", "STATE_NAME")

In [6]:
def clean_il_df(df):
    df = df[['STATE_ABBREVIATION', 'COUNTY_NAME', 'COUNTY_FIPS_CODE', 'STUDYYEAR', 'MHI', 'MCSA', 'MCINFANT', 'MCTODDLER', 'MCPRESCHOOL']]
    il_df = df[(df['STATE_ABBREVIATION'] == 'IL') & (df['STUDYYEAR'] == 2022)]
    il_df = il_df[(il_df['MCSA'].notna()) & (il_df['MCPRESCHOOL'].notna()) & (il_df['MCTODDLER'].notna()) & (il_df['MCINFANT'].notna())]

    return il_df

In [18]:
def grouped_il_bar_df(df):
    melt_df = df.melt(
        id_vars=['COUNTY_NAME'],
        value_vars=['MCSA', 'MCINFANT', 'MCTODDLER', 'MCPRESCHOOL'],
        var_name='age',
        value_name='price'
    )
    melt_df['age'] = melt_df['age'].str.replace('MC', '').str.lower()
    melt_df['age'] = melt_df['age'].str.replace('sa', 'schoolage')
    merged = pd.merge(melt_df, df[['COUNTY_NAME', 'MHI']], "left", "COUNTY_NAME")
    merged["adjusted price"] = merged['price'] * 52 / merged['MHI']

    return merged

In [70]:
il_df = clean_il_df(big_22_ndcp_df)
il_df = grouped_il_bar_df(il_df)

### Illinois, County-Level, Normalized

In [ ]:
groupedbar(il_df, "2022 Childcare Cost Normalized by County Median Household Income", "adjusted price", "COUNTY_NAME")

Income analysis for excluded states and counties

## Graph Set Two

This set of graphs are a collection of scatterplots that look at childcare cost burden for school age children (easily the least expensive, across the board) ploted against cost burden for care services for younger children, which is more specialized.

Once again, I did national and Illinois level graphs. I started just plotting schoolage against infantcare, but then I wondered if there would be noticeable differences between schoolage and the other two categories and did tricolor plots. I'm not super wowwed by any of them, so I would appreciate feedback on better graph types or whether this kind of graph should be included in my final project.

In [493]:
state_costs_df = state_avg_costs_df(state_lvl_df)
state_costs_df = pd.merge(state_costs_df, census_mhi_df, "left", "STATE_NAME")
state_costs_df['adj_infant'] = (state_costs_df["MEDIAN_INFANT_PRICE"] * 52) / state_costs_df['MHI']
state_costs_df['adj_toddler'] = (state_costs_df["MEDIAN_TODDLER_PRICE"] * 52) / state_costs_df['MHI']
state_costs_df['adj_preschool'] = (state_costs_df["MEDIAN_PRESCHOOL_PRICE"] * 52) / state_costs_df['MHI']
state_costs_df['adj_schoolage'] = (state_costs_df["MEDIAN_SCHOOLAGE_PRICE"] * 52) / state_costs_df['MHI']

In [494]:
def schoolage_v_infant_scatter(df, title):
    alt.Chart(df).mark_circle().encode(
        alt.X('adj_schoolage').scale(domain=(0, .3)).axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('adj_infant').scale(domain=(0, .3)).axis(format='%').title("Normalized Infantcare Cost"),
    ).properties(title=title).show()

### National, Infantcare vs Schoolage Care

In [495]:
schoolage_v_infant_scatter(state_costs_df, "School Age Childcare vs Infantcare Burden by State")

alt.Chart(...)

In [24]:
def schoolage_multi_scatter(df, title):
    chart = alt.Chart(df)
    
    infant = chart.mark_circle(color="blue", opacity=.5).encode(
        alt.X('adj_schoolage').scale(domain=(0, .3)).axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('adj_infant').scale(domain=(0, .3)).axis(format='%').title("Under-Schoolage Childcare Normalized Cost"),
    )

    toddler = chart.mark_circle(color="red", opacity=.5).encode(
        alt.X('adj_schoolage').scale(domain=(0, .3)).axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('adj_toddler').scale(domain=(0, .3)).axis(format='%').title("Under-Schoolage Childcare Normalized Cost"),
    )

    preschool = chart.mark_circle(color="yellow", opacity=.5).encode(
        alt.X('adj_schoolage').scale(domain=(0, .3)).axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('adj_preschool').scale(domain=(0, .3)).axis(format='%').title("Under-Schoolage Childcare Normalized Cost"),
    )

    layered = infant + toddler + preschool

    layered.properties(title=title).show()

### National, All Younger Care vs Schoolage Care

In [25]:
schoolage_multi_scatter(state_costs_df, "School Age Childcare vs Under 6 Childcare Burden by State")

alt.LayerChart(...)

In [26]:
il_df = clean_il_df(big_22_ndcp_df)
il_df['adj_infant'] = (il_df["MCINFANT"] * 52) / il_df['MHI']
il_df['adj_toddler'] = (il_df["MCTODDLER"] * 52) / il_df['MHI']
il_df['adj_preschool'] = (il_df["MCPRESCHOOL"] * 52) / il_df['MHI']
il_df['adj_schoolage'] = (il_df["MCSA"] * 52) / il_df['MHI']

### Illinois, Infantcare vs Schoolage Care

In [27]:
schoolage_v_infant_scatter(il_df, "Illinois School Age Childcare vs Infantcare Burden by County")

alt.Chart(...)

### Illinois, All Younger Care vs Schoolage Care

In [28]:
schoolage_multi_scatter(il_df, "Illinois School Age Childcare vs Under 6 Childcare Burden by County")

alt.LayerChart(...)

## Graph Set Three

This graph is a scatterplot that considers cost burden of childcare by cohort (School Age vs Preschool) and female labor participation rate for mothers with children in those respective categories.

I included regression lines, but the presence of outliers makes me skeptical of their quality, and the data doesn't seem to produce visible trends for either cluster. Would be curious to try this out with other states and see if that's still the case.

In [7]:
def get_il_w_normcost(df):
    il_df = clean_il_df(df)
    il_df['adj_infant'] = (il_df["MCINFANT"] * 52) / il_df['MHI']
    il_df['adj_toddler'] = (il_df["MCTODDLER"] * 52) / il_df['MHI']
    il_df['adj_preschool'] = (il_df["MCPRESCHOOL"] * 52) / il_df['MHI']
    il_df['adj_schoolage'] = (il_df["MCSA"] * 52) / il_df['MHI']

    return il_df

In [8]:
def get_flpr_df(df):

    female_labor_df = df[(df['STATE_ABBREVIATION'] == 'IL'
                                    ) & (df['STUDYYEAR'] == 2022)]
    female_labor_df = female_labor_df[(female_labor_df['MCSA'].notna()
                                    ) & (female_labor_df['MCPRESCHOOL'].notna()
                                            ) & (female_labor_df['MCTODDLER'].notna()
                                                ) & (female_labor_df['MCINFANT'].notna())]

    flpr_var = ['COUNTY_NAME', 'FLFPR_20to64', 'FLFPR_20to64_UNDER6', 'FLFPR_20to64_6to17',
                'FLFPR_20to64_UNDER6_6to17']

    female_labor_df = female_labor_df[flpr_var]

    flpr_var.pop(0)

    for col in flpr_var:
        female_labor_df[col] = female_labor_df[col] / 100

    return female_labor_df

In [9]:
il_df = get_il_w_normcost(big_22_ndcp_df)
female_labor_df = get_flpr_df(big_22_ndcp_df)
il_df = pd.merge(il_df, female_labor_df, 'left', 'COUNTY_NAME')

In [10]:
def labor_burden_scatter(df, title):
    chart = alt.Chart(df)

    preschool = chart.mark_circle(color='teal', opacity=.5).encode(
        alt.X('adj_preschool').axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('FLFPR_20to64_UNDER6:Q').axis(format='%').title("Maternal Labor Force Participation"),
    )

    preschool = preschool + preschool.transform_regression('adj_preschool', 'FLFPR_20to64_UNDER6').mark_line(color="teal")

    schoolage = chart.mark_circle(color='orange', opacity=.5).encode(
        alt.X('adj_schoolage').axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('FLFPR_20to64_6to17:Q').axis(format='%').title("Maternal Labor Force Participation"),
    )

    schoolage = schoolage + schoolage.transform_regression('adj_schoolage', 'FLFPR_20to64_6to17').mark_line(color="orange")

    layered = preschool + schoolage

    layered.properties(title=title).show()

In [11]:
labor_burden_scatter(il_df, "IL FLPR for Mothers of School Age and Under 6 Children")

alt.LayerChart(...)

## Graph Set Four

For this group I have made heat maps that look at childcare burden for preschool age children and female labor force participation. The first heatmap looks exclusively at female labor force participation for mothers with children under the age of 6. The second looks at the general female labor force participation rate (ages 20-64) to see if it's remarkably different. We see that it is in fact different, the rate appears to be lower for women who *don't* have very small children, which runs contrary to intuition.

In [8]:
def young_flpr_df(df):
    yflpr_df = df[(df['STUDYYEAR'] == 2022)]
    select_columns = ['STATE_NAME', 'COUNTY_NAME', 'COUNTY_FIPS_CODE', 'MHI', 'MCINFANT', 'MCTODDLER', 'MCPRESCHOOL', 'MCSA', 'FLFPR_20to64', 'FLFPR_20to64_UNDER6', 'FLFPR_20to64_6to17']
    yflpr_df = yflpr_df[select_columns]
    #'FLFPR_20to64_UNDER6_6to17'
    pct_tidy = ['FLFPR_20to64', 'FLFPR_20to64_UNDER6', 'FLFPR_20to64_6to17']

    for col in pct_tidy:
        yflpr_df[col] = yflpr_df[col] / 100

    adj_val = ['MCINFANT', 'MCTODDLER', 'MCPRESCHOOL', 'MCSA']

    for col in adj_val:
        nice_name = col[2:].lower()
        yflpr_df[f'adj_{nice_name}'] = (yflpr_df[col] * 52) / yflpr_df['MHI']

    return yflpr_df

In [287]:
yflpr_df = young_flpr_df(big_22_ndcp_df)

In [286]:
def flpr_heatmap(df, young_mothers, title):
    if young_mothers:
        y_var = 'FLFPR_20to64_UNDER6'
        y_title = ["Maternal Labor Force Participation Rate", "(Child Under Age Six)"]
    else:
        y_var = 'FLFPR_20to64'
        y_title = "Female Labor Force Participation Rate"
    domain = [1, 20, 40, 60, 80, 100]
    range_ = ["#befbd1", "#A5D9D2", "#6FC0CE", "#6A8DCE", "#5269CF", "#3847cd"]
    alt.Chart(df).mark_rect().encode(
        alt.X('adj_preschool:Q').bin(step=.01).axis(format="%").title("Preschool Age Childcare Cost Burden Normalized by MHI"),
        alt.Y(f'{y_var}:Q').bin(step=.05).scale(domain=(0.0, 1.0)).axis(format="%").title(y_title),
        alt.Color('count():Q').scale(domain=domain, range=range_).legend(title='Number of Counties')
    ).properties(title=title).show()

In [289]:
flpr_heatmap(yflpr_df, True, ["2022 Preschool Cost Burden vs. Female Labor Force Participation by County", "for Mothers of Children Under Six"])

alt.Chart(...)

In [288]:
flpr_heatmap(yflpr_df, False, ["2022 Preschool Cost Burden vs.", "General Female Labor Force Participation by County"])

alt.Chart(...)

## Graph Set Five

I wanted to do some kind of line graph analyzing trends in childcare prices over time. For the faceted graph I made, I focused only on prices for school age children, and I only did states that have complete data for the full range of years (2008-2022). Doing all the states side by side was too visually overwhelming, so I opted to group them by region. 

The way I've done it here uses way too many colors, and it's too confusing to differentiate states. I'm wondering if it's possible to do something analogous to a multi-panel scatter plot here.

In [46]:
def clear_incomplete_states(df):
    prices = ['MEDIAN_SCHOOLAGE_PRICE', 'MEDIAN_PRESCHOOL_PRICE', 'MEDIAN_TODDLER_PRICE', 'MEDIAN_INFANT_PRICE']
    df_clean = df.dropna(subset=prices)
    years_per_state = df_clean.groupby('STATE_NAME')['STUDYYEAR'].nunique()
    expected_years = df['STUDYYEAR'].nunique()
    states_with_all_years = years_per_state[years_per_state == expected_years].index
    df_clean = df_clean[df_clean['STATE_NAME'].isin(states_with_all_years)]

    return df_clean

In [47]:
def add_region(df):
    SOUTHEAST = ['Alabama', 'Florida', 'Kentucky', 'Louisiana', 'Tennessee', 'West Virginia']
    MIDWEST = ['Illinois', 'Kansas', 'Michigan', 'Minnesota', 'North Dakota', 'South Dakota', 'Wisconsin']
    WEST = ['Arizona', 'Oklahoma', 'Oregon', 'Utah', 'Washington']
    NORTHEAST = ['Connecticut', 'Delaware', 'Massachusetts', 'New Jersey']

    region_map = {}
    for state in NORTHEAST:
        region_map[state] = 'Northeast'
    for state in MIDWEST:
        region_map[state] = 'Midwest'
    for state in SOUTHEAST:
        region_map[state] = 'South'
    for state in WEST:
        region_map[state] = 'West'

    df['REGION'] = df['STATE_NAME'].map(region_map)

    return df

In [48]:
def time_trends_df(df):
    tt_df = df[df['TYPE'] == 'Center']
    tt_df = tt_df[['STATE_NAME', 'TYPE', 'STUDYYEAR', 'MEDIAN_SCHOOLAGE_PRICE', 'MEDIAN_PRESCHOOL_PRICE', 'MEDIAN_TODDLER_PRICE', 'MEDIAN_INFANT_PRICE']]
    tt_df = clear_incomplete_states(tt_df)
    tt_df = add_region(tt_df)

    return tt_df

In [49]:
tt_df = time_trends_df(state_lvl_df)

In [50]:
def time_trends(df, title, cohort):
    alt.Chart(df).mark_line().encode(
        alt.X('STUDYYEAR:O').title("Year"),
        alt.Y(f'{cohort}:Q').title("Median Weekly Childcare Cost for School Aged Children"),
        alt.Color('STATE_NAME:N')
    ).facet(facet='REGION:N', columns=2).properties(title=title).show()

In [110]:
tt_df.head()

STATE_NAME    TYPE  STUDYYEAR  MEDIAN_SCHOOLAGE_PRICE  \
0    Alabama  Center       2008                   94.10   
2    Alabama  Center       2009                   95.10   
4    Alabama  Center       2010                   94.43   
6    Alabama  Center       2011                   93.77   
8    Alabama  Center       2012                   93.10   

   MEDIAN_PRESCHOOL_PRICE  MEDIAN_TODDLER_PRICE  MEDIAN_INFANT_PRICE REGION  
0                   95.44                107.45               107.45  South  
2                   97.60                109.28               109.28  South  
4                   98.10                108.62               108.62  South  
6                   98.61                107.95               107.95  South  
8                   99.11                107.28               107.28  South

In [232]:
lst = list(tt_df['STATE_NAME'].unique())

In [236]:
lst

['Arizona',
 'Connecticut',
 'Delaware',
 'Kansas',
 'Massachusetts',
 'Michigan',
 'Minnesota',
 'New Jersey',
 'North Dakota',
 'Oklahoma',
 'Oregon',
 'South Dakota',
 'Tennessee',
 'Utah',
 'Washington',
 'West Virginia',
 'Wisconsin']

In [234]:
bye_states = ['Alabama', 'Florida', 'Kentucky', 'Louisiana', 'Illinois']
to_delete = []

for i, state in enumerate(lst):
    if state in bye_states:
        to_delete.append(i)

In [235]:
for i in reversed(to_delete):
    lst.pop(i)

In [57]:
lst

['Alabama',
 'Arizona',
 'Connecticut',
 'Delaware',
 'Kansas',
 'Massachusetts',
 'Michigan',
 'Minnesota',
 'New Jersey',
 'North Dakota',
 'Oklahoma',
 'Oregon',
 'South Dakota',
 'Tennessee',
 'Utah',
 'Washington',
 'West Virginia',
 'Wisconsin']

In [77]:
', '.join(lst)

'Alabama, Arizona, Connecticut, Delaware, Kansas, Massachusetts, Michigan, Minnesota, New Jersey, North Dakota, Oklahoma, Oregon, South Dakota, Tennessee, Utah, Washington, West Virginia, Wisconsin'

In [92]:
tt_df[tt_df['STUDYYEAR'] == 2022]['REGION'].value_counts()

REGION
Midwest      7
South        6
West         5
Northeast    4
Name: count, dtype: int64

In [98]:
list(tt_df['REGION'].unique())

['South', 'West', 'Northeast', 'Midwest']

In [237]:
def assign_color_scheme(df):
    seven_scheme = ["#4569ee", "#ff821d", "#3ff393", "#cb2f0d", "#26bce1", "#ecd12e", "#95fb51"]
    regions = list(df['REGION'].unique())
    region_lsts = []

    for region in regions:
        st_in_region = list(df[df['REGION'] == region]['STATE_NAME'].unique())
        region_lsts.append(st_in_region)

    color_range = []
    state_domain = []
    for region in region_lsts:
        for i, state in enumerate(region):
            color_range.append(seven_scheme[i])
            state_domain.append(state)

    return state_domain, color_range

In [106]:
lst.pop(0)

'Alabama'

In [238]:
# Create a common chart object
chart = alt.Chart(tt_df)

# Manual Color Scheme
state_domain, color_range = assign_color_scheme(tt_df)

# Draw the line
line = chart.mark_line().encode(
        alt.X('STUDYYEAR:O').title("Year"),
        alt.Y('MEDIAN_SCHOOLAGE_PRICE:Q').scale(domain=(0, 240)).title("Median Weekly Childcare Cost for School Aged Children"),
        alt.Color('STATE_NAME:N', legend=None, scale=alt.Scale(domain=state_domain, range=color_range))
        )

# Use the `argmax` aggregate to limit the dataset to the final value
label = chart.encode(
    alt.X('max(STUDYYEAR):O'),
    alt.Y('MEDIAN_SCHOOLAGE_PRICE:Q').aggregate(argmax='STUDYYEAR'),
    text='STATE_NAME'
)

# Create a text label
text = label.mark_text(align='left', dx=10).transform_filter(alt.FieldOneOfPredicate(field='STATE_NAME', oneOf=lst)
)
unoverlap_1 = label.mark_text(align='left', dx=10, dy=12).transform_filter(alt.FieldOneOfPredicate(field='STATE_NAME', oneOf=['Florida', 'Alabama'])
)
unoverlap_2 = label.mark_text(align='left', dx=10, dy=3).transform_filter(alt.FieldOneOfPredicate(field='STATE_NAME', oneOf=['Kentucky', 'Illinois'])
)
unoverlap_3 = label.mark_text(align='left', dx=10, dy=-6).transform_filter(alt.FieldOneOfPredicate(field='STATE_NAME', oneOf=['Louisiana'])
)

# Draw the chart with all the layers combined
final = line + text + unoverlap_1 + unoverlap_2 + unoverlap_3

final.facet(facet=alt.Facet(
        'REGION:N',
        title=None), columns=2).properties(title="School Age Childcare Costs 2008-2022 by State").resolve_scale(x= 'independent', y='independent').show()

alt.FacetChart(...)

In [80]:
time_trends(tt_df, "School Age Childcare Costs 2008-2022 by State", 'MEDIAN_SCHOOLAGE_PRICE')

alt.FacetChart(...)

In [14]:
earn_df.head()

STATE_NAME       COUNTY_NAME  COUNTY_FIPS_CODE    FME  FEMP_M
8941   Illinois      Adams County             17001  33114   0.402
8956   Illinois  Alexander County             17003  29511   0.240
8971   Illinois       Bond County             17005  25597   0.326
8986   Illinois      Boone County             17007  33929   0.338
9001   Illinois      Brown County             17009  36758   0.293

In [59]:
earn_df = big_22_ndcp_df[['STATE_NAME', 'COUNTY_NAME', 'COUNTY_FIPS_CODE', 'FME', 'FEMP_M']]

In [60]:
earn_df['FEMP_M'] = earn_df['FEMP_M'] / 100

C:\Users\calli\AppData\Local\Temp\ipykernel_54988\1214740423.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  earn_df['FEMP_M'] = earn_df['FEMP_M'] / 100


In [61]:
def earn_industry_df(industry):
    '''
    female median earnings vs people with fancy jobs
    '''
    earn_df = big_22_ndcp_df[big_22_ndcp_df['STUDYYEAR'] == 2022]
    earn_df = earn_df[['STATE_NAME', 'COUNTY_NAME', 'COUNTY_FIPS_CODE', 'FME', f'{industry}']]
    #earn_df = earn_df[earn_df['STATE_NAME'] == 'Illinois']
    earn_df[f'{industry}'] = earn_df[f'{industry}'] / 100

    return earn_df


In [30]:
earn_df = earn_industry_df('EMP_SERVICE')

In [19]:
earn_df.shape

(3221, 5)

In [62]:
def earn_industry_scatter(df, title, industry):
    chart = alt.Chart(df, title=alt.Title(title,
                                          subtitle=["Select industries include management, business,",
                                                    "science, and arts."]))
    
    dots = chart.mark_circle(color="#ff821d", opacity=.4,).encode(
        alt.X(f'{industry}').axis(format='%').title("Percentage of Women Employed in Select Industries"),
        alt.Y('FME').title("Female Median Earnings in Dollars"),
        )
    
    regression = dots.transform_regression(f'{industry}', 'FME').mark_line(color="#cb2f0d")

    final = dots + regression

    final.show()


In [62]:
def gender_comparison(df, industry, gender):
    chart = alt.Chart(df)
    
    dots = chart.mark_circle(color="#ff821d", opacity=.4, title=alt.Title(title)).encode(
        alt.X(f'{industry}').axis(format='%').title("PCT Fancy Job"),
        alt.Y('FME').title("Female Median Earnings"),
        )
    
    regression = dots.transform_regression(f'{industry}', 'FME').mark_line(color="#cb0dae")

    chart2 = alt.Chart(df)
    
    dots2 = chart2.mark_circle(color="#ff821d", opacity=.4).encode(
    alt.X(f'{gender}').axis(format='%').title("PCT Fancy Job"),
    alt.Y('FME').title("Female Median Earnings"),
    )
    
    regression2 = dots.transform_regression(f'{gender}', 'FME').mark_line(color="#cb0dae")

    final = regression + regression2

    final.show()

In [63]:
earn_df = earn_industry_df('FEMP_M')

In [467]:
alt.data_transformers.enable("vegafusion")

DataTransformerRegistry.enable('vegafusion')

In [65]:
earn_industry_scatter(earn_df, "Female Median Earnings and Percentage of Women Employed in Select Industries", 'FEMP_M')

alt.LayerChart(...)

In [40]:
gender_comparison(earn_df, 'EMP_M', 'FEMP_M')

alt.LayerChart(...)

In [244]:
#categorize based on MLFPR, then look at family poverty rates, fancy jobs, and female median earnings
yflpr_df = young_flpr_df(big_22_ndcp_df)
yflpr_df.head()

STATE_NAME     COUNTY_NAME  COUNTY_FIPS_CODE    MHI  MCINFANT  MCTODDLER  \
14    Alabama  Autauga County              1001  68315    145.80     138.72   
29    Alabama  Baldwin County              1003  71039    133.30     129.14   
44    Alabama  Barbour County              1005  39712    121.85     116.65   
59    Alabama     Bibb County              1007  50669    136.43     132.47   
74    Alabama   Blount County              1009  57440    145.92     150.45   

    MCPRESCHOOL    MCSA  FLFPR_20to64  FLFPR_20to64_UNDER6  \
14       124.97  113.52         0.684                0.653   
29       122.89  111.43         0.711                0.692   
44       110.40  103.94         0.646                0.807   
59       128.72  124.97         0.675                0.750   
74       137.95  123.81         0.648                0.806   

    FLFPR_20to64_6to17  adj_infant  adj_toddler  adj_preschool    adj_sa  
14               0.741    0.110980     0.105591       0.095125  0.086409  
29               0.789    0.097575     0.094529       0.089955  0.081566  
44               0.770    0.159554     0.152745       0.144561  0.136102  
59               0.558    0.140014     0.135950       0.132101  0.128253  
74               0.738    0.132100     0.136201       0.124885  0.112084

In [138]:
yflpr_df['adj_preschool'].dropna().shape

(2670,)

(3221, 14)

In [245]:
#"Cost-Participation"
def sort_counties(row):
    if (row['adj_preschool'] >= .16) & (row['FLFPR_20to64_UNDER6'] >= .5):
        return "High-High"
    elif (row['adj_preschool'] < .16) & (row['FLFPR_20to64_UNDER6'] >= .5):
        return "Low-High"
    elif (row['adj_preschool'] >= .16) & (row['FLFPR_20to64_UNDER6'] < .5):
        return "High-Low"
    elif (row['adj_preschool'] < .16) & (row['FLFPR_20to64_UNDER6'] < .5):
        return "Low-Low"
    else:
        return "Unclassified"

yflpr_df['Classification'] = yflpr_df.apply(sort_counties, axis=1)

In [198]:
yflpr_df.head()

STATE_NAME     COUNTY_NAME  COUNTY_FIPS_CODE    MHI  MCINFANT  MCTODDLER  \
14    Alabama  Autauga County              1001  68315    145.80     138.72   
29    Alabama  Baldwin County              1003  71039    133.30     129.14   
44    Alabama  Barbour County              1005  39712    121.85     116.65   
59    Alabama     Bibb County              1007  50669    136.43     132.47   
74    Alabama   Blount County              1009  57440    145.92     150.45   

    MCPRESCHOOL    MCSA  FLFPR_20to64  FLFPR_20to64_UNDER6  \
14       124.97  113.52         0.684                0.653   
29       122.89  111.43         0.711                0.692   
44       110.40  103.94         0.646                0.807   
59       128.72  124.97         0.675                0.750   
74       137.95  123.81         0.648                0.806   

    FLFPR_20to64_6to17  adj_infant  adj_toddler  adj_preschool    adj_sa  \
14               0.741    0.110980     0.105591       0.095125  0.086409   
29               0.789    0.097575     0.094529       0.089955  0.081566   
44               0.770    0.159554     0.152745       0.144561  0.136102   
59               0.558    0.140014     0.135950       0.132101  0.128253   
74               0.738    0.132100     0.136201       0.124885  0.112084   

   Classification  
14       Low-High  
29       Low-High  
44       Low-High  
59       Low-High  
74       Low-High

In [246]:
yflpr_df = yflpr_df[yflpr_df['Classification'] != 'Unclassified']

In [247]:
filtered = yflpr_df[["STATE_NAME", "COUNTY_NAME", 'COUNTY_FIPS_CODE', "MHI", "FLFPR_20to64_UNDER6", "adj_preschool", "Classification"]]

df = big_22_ndcp_df[big_22_ndcp_df['STUDYYEAR']==2022]

df = df[["COUNTY_FIPS_CODE", "FEMP_M", "PR_F", "FME"]]

final = filtered.merge(df, "left", "COUNTY_FIPS_CODE")

In [201]:
final.head()

STATE_NAME     COUNTY_NAME  COUNTY_FIPS_CODE    MHI  FLFPR_20to64_UNDER6  \
0    Alabama  Autauga County              1001  68315                0.653   
1    Alabama  Baldwin County              1003  71039                0.692   
2    Alabama  Barbour County              1005  39712                0.807   
3    Alabama     Bibb County              1007  50669                0.750   
4    Alabama   Blount County              1009  57440                0.806   

   adj_preschool Classification  FEMP_M  PR_F    FME  
0       0.095125       Low-High    44.2   8.3  30975  
1       0.089955       Low-High    40.1   7.0  30953  
2       0.144561       Low-High    33.6  20.8  27128  
3       0.132101       Low-High    34.0  16.3  24206  
4       0.124885       Low-High    37.0  10.2  29955

In [248]:
final['FEMP_M'] = final['FEMP_M'] / 100
final['PR_F'] = final['PR_F'] / 100
final.head()

STATE_NAME     COUNTY_NAME  COUNTY_FIPS_CODE    MHI  FLFPR_20to64_UNDER6  \
0    Alabama  Autauga County              1001  68315                0.653   
1    Alabama  Baldwin County              1003  71039                0.692   
2    Alabama  Barbour County              1005  39712                0.807   
3    Alabama     Bibb County              1007  50669                0.750   
4    Alabama   Blount County              1009  57440                0.806   

   adj_preschool Classification  FEMP_M   PR_F    FME  
0       0.095125       Low-High   0.442  0.083  30975  
1       0.089955       Low-High   0.401  0.070  30953  
2       0.144561       Low-High   0.336  0.208  27128  
3       0.132101       Low-High   0.340  0.163  24206  
4       0.124885       Low-High   0.370  0.102  29955

In [250]:
final['FME'].max()

np.int64(74250)

In [251]:
dt = {}

for condition in ['FEMP_M', 'PR_F', 'FME']:
    dt[condition] = (final[condition].min(), final[condition].max())

print(dt)

{'FEMP_M': (np.float64(0.0), np.float64(0.759)), 'PR_F': (np.float64(0.0), np.float64(0.515)), 'FME': (np.int64(8724), np.int64(74250))}


In [280]:
def econ_condition_mscatter(df, condition, title, range):
    chart = alt.Chart(df)

    if (condition == 'FME') or (condition == 'MHI'):
        form = '.0f'
    else:
        form='%'
    
    mscatter = chart.mark_circle(opacity=.5).encode(
        alt.X(f'{condition}').axis(format=form).scale(domain=range).title(f"{title}"),
        alt.Y('FLFPR_20to64_UNDER6').axis(format='%').scale(domain=(0, 1)).title("LPR for Mothers of Young Children"),
        alt.Color('Classification', legend=None, scale=alt.Scale(range=["#7bda3c", "#ff821d", "#2f9df5", "#cb3bc6"]))
    )

    mscatter.facet(facet=alt.Facet('Classification', title=None), columns=2).resolve_scale(x= 'independent', y='independent').properties(title=title).show()

In [281]:
econ_condition_mscatter(final, 'FEMP_M', "Pct Women Employed in Education-Intensive Industries", dt['FEMP_M'])

alt.FacetChart(...)

In [282]:
econ_condition_mscatter(final, 'PR_F', "Pct Families Below Poverty Line", dt['PR_F'])

alt.FacetChart(...)

In [283]:
econ_condition_mscatter(final, 'FME', "Female Median Earnings", dt['FME'])

alt.FacetChart(...)

In [ ]:
chart = alt.Chart(final)

mscatter = chart.mark_circle(opacity=.5).encode(
    alt.X("FEMP_M").axis(format='%'),
    alt.Y('FME'),
    alt.Color('Classification', scale=alt.Scale(range=["#7bda3c", "#ff821d", "#2f9df5", "#cb3bc6"]))
)

mscatter.facet(facet='Classification', columns=2).resolve_scale(x= 'independent', y='independent').show()

alt.FacetChart(...)

In [210]:
final[final['Classification'] == 'Low-Low'].sort_values('FLFPR_20to64_UNDER6')

STATE_NAME       COUNTY_NAME  COUNTY_FIPS_CODE    MHI  \
454            Idaho      Camas County             16025  63750   
395          Georgia    Quitman County             13239  38889   
1548  North Carolina       Hyde County             37095  43724   
1357        Nebraska  McPherson County             31117  58250   
2083           Texas     Borden County             48033  80625   
...              ...               ...               ...    ...   
2322            Utah  Box Elder County             49003  72769   
2000       Tennessee   Grainger County             47057  47098   
2410        Virginia     Nelson County             51125  64028   
2652         Wyoming     Carbon County             56007  65196   
1567  North Carolina     Onslow County             37133  59976   

      FLFPR_20to64_UNDER6  adj_preschool Classification  FEMP_M   PR_F    FME  
454                 0.000       0.091846        Low-Low   0.366  0.024  25250  
395                 0.000       0.136388        Low-Low   0.174  0.075  24297  
1548                0.000       0.130809        Low-Low   0.304  0.256  17669  
1357                0.000       0.145064        Low-Low   0.336  0.042  15833  
2083                0.000       0.090295        Low-Low   0.322  0.016  30833  
...                   ...            ...            ...     ...    ...    ...  
2322                0.493       0.120094        Low-Low   0.349  0.060  24826  
2000                0.493       0.121449        Low-Low   0.383  0.139  24172  
2410                0.496       0.128124        Low-Low   0.447  0.091  31169  
2652                0.497       0.105857        Low-Low   0.300  0.102  28172  
1567                0.499       0.111723        Low-Low   0.406  0.110  26533  

[155 rows x 10 columns]

In [284]:
final["Classification"].value_counts()

Classification
Low-High     2071
High-High     389
Low-Low       155
High-Low       55
Name: count, dtype: int64

In [285]:
55 / (2071 + 389 + 155 + 55)

0.020599250936329586

In [ ]:
toddler = chart.mark_circle(color=, opacity=.5).encode(
        alt.X('PR_F').scale(domain=(0, .3)).axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('FLFPR_20to64_UNDER6').scale(domain=(0, .3)).axis(format='%').title("Under-Schoolage Childcare Normalized Cost"),
    )

    preschool = chart.mark_circle(color=, opacity=.5).encode(
        alt.X('FME').axis(format='%').title("Normalized Schoolage Childcare Cost"),
        alt.Y('FLFPR_20to64_UNDER6').axis(format='%').title("Under-Schoolage Childcare Normalized Cost"),
    )

    layered = infant + toddler + preschool

    layered.properties(title=title).show()

In [293]:
grouped_df

STATE_NAME        age   price    MHI  adjusted price
0          Alabama     infant  136.01  59674        0.118519
1          Arizona     infant  270.00  74568        0.188285
2       California     infant  379.21  91551        0.215387
3         Colorado     infant  377.40  89302        0.219758
4      Connecticut     infant  350.00  88429        0.205815
..             ...        ...     ...    ...             ...
159           Utah  schoolage  163.68  89168        0.095453
160       Virginia  schoolage  155.25  85873        0.094011
161     Washington  schoolage  199.61  91306        0.113681
162  West Virginia  schoolage  146.45  54329        0.140172
163      Wisconsin  schoolage  205.00  70996        0.150149

[164 rows x 5 columns]

In [295]:
def code_rank(row):
    '''
    Numerical codings to make distinguish ranking types with greater ease.
    '''
    if row['variable'] == "Restrictiveness":
        return 0
    elif row['variable'] == "Quality":
        return 1
    else:
        return 2

def reg_rankings_df(cohort):
    '''
    Create regulation and cost burden rankings for parallel coordinate plot.
    '''
    df = grouped_df
    reg_df = regulations_df

    #filter by cohort and sort by cost burden descending
    parallel_df = df[df["age"] == f'{cohort}'].sort_values(
        'adjusted price', ascending=False)
    #create cost ranking by attaching 1-41 on sorted df
    ranking = list(range(1,42))
    parallel_df['Cost Burden'] = ranking

    #filter to five most expensive and five least expensive
    parallel_df = parallel_df[(
        parallel_df["Cost Burden"] < 6) | (parallel_df["Cost Burden"] > 36)]
    
    #merge in regulatory rankings
    parallel_df = parallel_df.merge(reg_df, "left", "STATE_NAME")

    #change to long form
    parallel_df = pd.melt(parallel_df, id_vars=['STATE_NAME'],
                          value_vars=['Restrictiveness', 'Quality', 'Cost Burden'])
    
    parallel_df['Rank_Type'] = parallel_df.apply(code_rank, axis=1)

    return parallel_df


In [296]:
parallel_df = reg_rankings_df('schoolage')

In [297]:
parallel_df.head()

STATE_NAME         variable  value  Rank_Type
0     Nevada  Restrictiveness     44          0
1    Montana  Restrictiveness     42          0
2  Wisconsin  Restrictiveness     11          0
3  Minnesota  Restrictiveness      7          0
4   New York  Restrictiveness      2          0

In [6]:
def sort_counties(row): #helper
    '''
    Buckets counties into "Cost-Participation" groups.
    '''
    if (row['adj_preschool'] >= .16) & (row['FLFPR_20to64_UNDER6'] >= .5):
        return "High-High"
    elif (row['adj_preschool'] < .16) & (row['FLFPR_20to64_UNDER6'] >= .5):
        return "Low-High"
    elif (row['adj_preschool'] >= .16) & (row['FLFPR_20to64_UNDER6'] < .5):
        return "High-Low"
    elif (row['adj_preschool'] < .16) & (row['FLFPR_20to64_UNDER6'] < .5):
        return "Low-Low"
    else:
        return "Unclassified"

def county_df():
    '''
    Factors for county analysis scatter plots.
    '''
    yflpr_df = young_flpr_df(big_22_ndcp_df)
    yflpr_df['Classification'] = yflpr_df.apply(sort_counties, axis=1)
    yflpr_df = yflpr_df[yflpr_df['Classification'] != 'Unclassified']
    filtered = yflpr_df[["STATE_NAME", "COUNTY_NAME", 'COUNTY_FIPS_CODE', "MHI", "FLFPR_20to64_UNDER6", "adj_preschool", "Classification"]]
    df = big_22_ndcp_df[big_22_ndcp_df['STUDYYEAR']==2022]
    df = df[["COUNTY_FIPS_CODE", "FEMP_M", "PR_F", "FME"]]
    final = filtered.merge(df, "left", "COUNTY_FIPS_CODE")
    final['FEMP_M'] = final['FEMP_M'] / 100
    final['PR_F'] = final['PR_F'] / 100

    return final

In [9]:
cdf = county_df()
cdf.head()

STATE_NAME     COUNTY_NAME  COUNTY_FIPS_CODE    MHI  FLFPR_20to64_UNDER6  \
0    Alabama  Autauga County              1001  68315                0.653   
1    Alabama  Baldwin County              1003  71039                0.692   
2    Alabama  Barbour County              1005  39712                0.807   
3    Alabama     Bibb County              1007  50669                0.750   
4    Alabama   Blount County              1009  57440                0.806   

   adj_preschool Classification  FEMP_M   PR_F    FME  
0       0.095125       Low-High   0.442  0.083  30975  
1       0.089955       Low-High   0.401  0.070  30953  
2       0.144561       Low-High   0.336  0.208  27128  
3       0.132101       Low-High   0.340  0.163  24206  
4       0.124885       Low-High   0.370  0.102  29955

In [306]:
yflpr_df = young_flpr_df(big_22_ndcp_df)
yflpr_df['Classification'] = yflpr_df.apply(sort_counties, axis=1)
yflpr_df = yflpr_df[yflpr_df['Classification'] != 'Unclassified']
filtered = yflpr_df[["STATE_NAME", "COUNTY_NAME", 'COUNTY_FIPS_CODE', "MHI", "FLFPR_20to64_UNDER6", "adj_preschool", "Classification"]]
df = big_22_ndcp_df[big_22_ndcp_df['STUDYYEAR']==2022]
df = df[["COUNTY_FIPS_CODE", "FEMP_M", "PR_F", "FME"]]
final = filtered.merge(df, "left", "COUNTY_FIPS_CODE")
final['FEMP_M'] = final['FEMP_M'] / 100
final['PR_F'] = final['PR_F'] / 100
final.head()

STATE_NAME     COUNTY_NAME  COUNTY_FIPS_CODE    MHI  FLFPR_20to64_UNDER6  \
0    Alabama  Autauga County              1001  68315                0.653   
1    Alabama  Baldwin County              1003  71039                0.692   
2    Alabama  Barbour County              1005  39712                0.807   
3    Alabama     Bibb County              1007  50669                0.750   
4    Alabama   Blount County              1009  57440                0.806   

   adj_preschool Classification  FEMP_M   PR_F    FME  
0       0.095125       Low-High   0.442  0.083  30975  
1       0.089955       Low-High   0.401  0.070  30953  
2       0.144561       Low-High   0.336  0.208  27128  
3       0.132101       Low-High   0.340  0.163  24206  
4       0.124885       Low-High   0.370  0.102  29955

In [ ]:
def domain_dict(df, condition): #helper
    '''
    Creates domain dictionaries for charts.
    '''
    dt = {}

    for condition in ['FEMP_M', 'PR_F', 'FME']:
        dt[condition] = (df[condition].min(), df[condition].max())

    return dt

def econ_condition_mscatter(condition, title):
    '''
    Scatter plots with binned counties on "Cost-Maternal LFPR"
    '''
    df = cdf
    range = domain_dict(df, condition)
    chart = alt.Chart(df)

    #formatting guidance for pct vs nonpct variables
    if (condition == 'FME') or (condition == 'MHI'):
        form = '.0f'
    else:
        form='%'
    
    mscatter = chart.mark_circle(opacity=.5).encode(
        alt.X(f'{condition}').axis(format=form).scale(domain=range[condition]).title(f"{title}"),
        alt.Y('FLFPR_20to64_UNDER6').axis(format='%').scale(domain=(0, 1)).title(
            "FLPR for Mothers of Young Children"),
        alt.Color('Classification', legend=None, scale=alt.Scale(
            range=["#7bda3c", "#ff821d", "#2f9df5", "#cb3bc6"]))
    )

    mscatter.facet(
        facet=alt.Facet('Classification', title=None), columns=2).resolve_scale(
        x= 'independent', y='independent').properties(title=title).show()

In [11]:
econ_condition_mscatter('FEMP_M', '--')

SchemaValidationError: '{'FEMP_M': [0.0, 0.759], 'PR_F': [0.0, 0.515], 'FME': [8724.0, 74250.0]}' is an invalid value for `domain`. Valid values are of type 'array' or 'string'.

'unaggregated' was expectedAdditional properties are not allowed ('FEMP_M', 'FME', 'PR_F' were unexpected)'param' is a required property
'unionWith' is a required property
'expr' is a required property

alt.FacetChart(...)